# Prepare Species occurrence range: climate type data from TRY for use

The Species occurrence range: climate type data from TRY informs on the climate zone or climatic conditions a plant occurs in.

*If you intend to clean more than one or two traits, we recommend the use
of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Species occurrence range: climate type"]


To get an overview of the data, we convert sort the values and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


It looks like a good idea to remove purely numeric values.

In [ ]:
oriVals[!grepl("[[:lower:]]", oriVals)] <- NA


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
# create a vector containing the search strings to look for
searchNames <- c(
	"(^|\\s)continental",
	"sub-?continental",
	"maritime",
	"^arc|polar",
	"sub-?arctic|tundra|^tun/",
	"boreal|taiga|bor",
	"temperate|te?mp$|cfa|cfb",
	"(^|\\s)medi(terrane(an)?|$)",
	"sub-?medi(terrane(an)?|$)",
	"^(tropical|trop|tr)",
	"sub-?tropical|sub-?trop",
	"forests",
	"savanna|trsav",
	"steppe",
	"desert",
	"(^|/|_|\\s)alp(ine|$)",
	"sub-?alpine",
	"montane|mountains",
	"arid|dry|xeric",
	"humid|wet|moist|cfa|cfb",
	"monsoon"
)


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like corrected searchNames
colnames(searchResults) <- c(
	"continental",
	"subcontinental",
	"maritime",
	"polar",
	"subpolar",
	"boreal",
	"temperate",
	"mediterranean",
	"submediterranean",
	"tropical",
	"subtropical",
	"forest",
	"savanna",
	"steppe",
	"desert",
	"alpine",
	"subalpine",
	"montane",
	"arid",
	"humid",
	"monsoon"
)


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
oriVals[rowSums(searchResults) < 1]

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


Now, we can create new strings with the cleaned values and add them to the observations. To
not remove the original entries, we will create a new column called "CleanedValueStr".

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
newVals <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[searchResults[x, ]], collapse = ",")
})
newVals[newVals == ""] <- NA

# integrate into TRY
TRY[TraitName == "", CleanedValueStr := newVals]


Although not necessary, we may change the trait name.

In [ ]:
TRY[TraitName == "Species occurrence range: climate type", TraitName := "Plant climate zone"]


Let's write the data to a file.

In [ ]:
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
